In [1]:
import sys, logging
from pathlib import Path
import pandas as pd

In [2]:
# Define the project root and add it to the path so we can run HECTRE.
PROJ_ROOT = Path('..', '..').resolve()
sys.path.insert(0, str(PROJ_ROOT))
print(sys.path)

['/Users/jan535/code/HECTRE', '/opt/homebrew/Cellar/python@3.11/3.11.5/Frameworks/Python.framework/Versions/3.11/lib/python311.zip', '/opt/homebrew/Cellar/python@3.11/3.11.5/Frameworks/Python.framework/Versions/3.11/lib/python3.11', '/opt/homebrew/Cellar/python@3.11/3.11.5/Frameworks/Python.framework/Versions/3.11/lib/python3.11/lib-dynload', '', '/Users/jan535/code/HECTRE/.venv/lib/python3.11/site-packages']


In [3]:
# Reload the notebook if imported modules are modified.
%load_ext autoreload
%autoreload 2

In [4]:
# Import HECTRE and disable logging. We'll be creating a custom report in this notebook.
from hectre.metrics import accuracy
logging.disable()

In [5]:
TESTING=True
TEST_ROOT = Path(PROJ_ROOT, 'hectre', 'tests', 'test_data')
control_cdfs = Path(TEST_ROOT, 'cdfs', 'eval_report').iterdir()
eval_data = {}
for control_cdf_path in control_cdfs:
    slug = control_cdf_path.stem.lower()
    pdf_path = Path(TEST_ROOT, slug + '.pdfdata')
    pdf_path_input = str(pdf_path)
    picos_input = "EASI-50;EASI-75;EASI-90"
    cdf_path_input = str(control_cdf_path)
    control_cdf = pd.read_csv(cdf_path_input)
    if TESTING:
        test_cdf = pd.read_csv(Path(TEST_ROOT, 'cdfs', 'eval_report_test_cdfs', control_cdf_path.name).resolve())
    else:
        test_cdf = accuracy.accuracy_extract_test(pdf_path_input, picos_input)
    acc = accuracy.cdf_accuracy(
        test_cdf,
        control_cdf,
        slug
    )
    eval_data[slug] = acc

Index(['ARM.TRT', 'ARM.DOSE', 'ARM.REGIMEN', 'ENDPOINT', 'ARM.TIME1',
       'primary_key', 'match_key', 'sample'],
      dtype='object')
Index(['ARM.TRT', 'ARM.DOSE', 'ARM.REGIMEN', 'ENDPOINT', 'ARM.TIME1',
       'primary_key', 'match_key', 'sample'],
      dtype='object')


In [6]:
print(eval_data.keys())

dict_keys(['287_silverberg_2021', '286_wollenberg_2021'])


In [7]:
wol = eval_data['286_wollenberg_2021']

In [8]:
print(wol.keys())

dict_keys(['comparison', 'lit_acc_pct', 'num_control_rows', 'matched_control_rows', 'clin_data_col_accs'])


# HECTRE Performance Evaluation Report

In [9]:
# Stacked DF stylization
def set_index_colors(df, index_styles):
    # DataFrame of styles
    df1 = pd.DataFrame('', index=df.index, columns=df.columns)
    for index_style in index_styles:
        mask = df.index.isin([index_style['value']], level=index_style['name'])
        df1[mask] = f"background-color: {index_style['color']};"
    return df1
    # # Subset your original dataframe with condition
    # df_ = df[df.index.get_level_values(index_name) == index_val]
    # # Pass the subset dataframe index and column to pd.IndexSlice
    # slice_ = pd.IndexSlice[df_.index, df_.columns]
    # # Style the dataframe
    # s = df.style.set_properties(**{'background-color': color}, subset=slice_)
    # return s

In [10]:
pd.set_option('display.max_rows', 200)
pd.set_option('display.max_columns', 100)
for slug, extraction in eval_data.items():
    print(slug)
    print(f"Literature data accuracy: {extraction['lit_acc_pct']:.2f}%")
    print("STACKED DF")
    index_styles = [
        {
            'name': 'sample',
            'value': 'similarity',
            'color': 'orange'
        },
        {
            'name': 'sample',
            'value': 'test',
            'color': 'skyblue'
        },
        {
            'name': 'sample',
            'value': 'control',
            'color': 'pink'
        },
        
    ]
    stacked_df = extraction['comparison']['stacked_df']
    stacked_df = stacked_df.style.apply(set_index_colors,axis=None, index_styles=index_styles)
    display(stacked_df)
    print("TEST SIMILARITY TO CONTROL (%)")
    display(extraction['comparison']['comp_values_clin'])

287_silverberg_2021
Literature data accuracy: 85.07%
STACKED DF


TEST SIMILARITY TO CONTROL (%)


ARM.BLIND  \
ARM.TRT      ARM.DOSE ARM.REGIMEN ENDPOINT ARM.TIME1 primary_key              
placebo      0        q2w         easi     0         0                  100   
                                           2         1                  100   
                                           4         2                  100   
                                           6         3                  100   
                                           8         4                  100   
                                           10        5                  100   
                                           12        6                  100   
                                           14        7                  100   
                                           16        8                  100   
tralokinumab 600      q2w         easi     0         9                  100   
             300      q2w         easi     2         10                   0   
                                           4         11                   0   
                                           6         12                   0   
                                           8         13                   0   
                                           10        14                   0   
                                           12        15                   0   
                                           14        16                   0   
                                           16        17                   0   
placebo      0        q2w         easi75   2         18                   0   
                                           4         19                   0   
                                           6         20                   0   
                                           8         21                   0   
                                           10        22                   0   
                                           12        23                   0   
                                           14        24                   0   
                                           16        25                   0   
tralokinumab 300      q2w         easi75   2         26                   0   
                                           4         27                   0   
                                           6         28                   0   
                                           8         29                   0   
                                           10        30                   0   
                                           12        31                   0   
                                           14        32                   0   
                                           16        33                   0   
placebo      0        q2w         scorad   0         34                   0   
                                           2         35                   0   
                                           4         36                   0   
                                           6         37                   0   
                                           8         38                   0   
                                           10        39                   0   
                                           12        40                   0   
                                           14        41                   0   
                                           16        42                   0   
tralokinumab 600      q2w         scorad   0         43                   0   
             300      q2w         scorad   2         44                   0   
                                           4         45                   0   
                                           6         46                   0   
                                           8         47                   0   
                                           10        48                   0   
                                     

286_wollenberg_2021
Literature data accuracy: 74.60%
STACKED DF


TEST SIMILARITY TO CONTROL (%)


ARM.BLIND  \
ARM.TRT      ARM.DOSE ARM.REGIMEN ENDPOINT ARM.TIME1 primary_key              
placebo      0        q2w         easi75   2         0                  100   
                                           4         1                  100   
                                           6         2                  100   
                                           8         3                  100   
                                           10        4                  100   
                                           12        5                  100   
                                           14        6                  100   
                                           16        7                  100   
tralokinumab 300      q2w         easi75   2         8                  100   
                                           4         9                  100   
                                           6         10                 100   
                                           8         11                 100   
                                           10        12                 100   
                                           12        13                 100   
                                           14        14                 100   
                                           16        15                   0   
                                           52        16                   0   
                      q4w         easi75   52        17                   0   
placebo      0        q2w         easi75   52        18                   0   
                                  easi50   2         19                   0   
                                           4         20                   0   
                                           6         21                   0   
                                           8         22                   0   
                                           10        23                   0   
                                           12        24                   0   
                                           14        25                   0   
                                           16        26                   0   
tralokinumab 300      q2w         easi50   2         27                   0   
                                           4         28                   0   
                                           6         29                   0   
                                           8         30                   0   
                                           10        31                   0   
                                           12        32                   0   
                                           14        33                   0   
                                           16        34                   0   
placebo      0        q2w         easi90   2         35                   0   
                                           4         36                   0   
                                           6         37                   0   
                                           8         38                   0   
                                           10        39                   0   
                                           12        40                   0   
                                           14        41                   0   
                                           16        42                   0   
tralokinumab 300      q2w         easi90   2         43                   0   
                                           4         44                   0   
                                           6         45                   0   
                                           8         46                   0   
                                           10        47                   0   
                                           12        48                   0   
                                     